##Import data & libraries

In [15]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np
import random
#import missingno as msno
#from google.colab import data_table
#from tabulate import tabulate
import scipy.stats as st
import matplotlib.patches as mpl_patches
import warnings
warnings.filterwarnings("ignore")
from scipy.stats import describe
import matplotlib.cm as cm
import matplotlib.lines as mlines
from scipy.stats import pearsonr
# !pip install powerbiclient
from tqdm import tqdm

### Funciones para explorar correlaciones

In [27]:
def heatmap(df):
    plt.figure(figsize=(70,70))
    plt.rc('xtick', labelsize=40) 
    plt.rc('ytick', labelsize=40) 
    return sns.heatmap(df.corr(method='spearman'), annot=True, square=True, cmap='coolwarm', annot_kws={'size': 10})

def correlation_1_vs_all(df, feature, threshold):
    pd.set_option('display.max_rows', None)
    df = df.corr().abs().unstack().sort_values(kind="quicksort", ascending=False).reset_index()
    df.rename(columns={"level_0": "Feature 1", "level_1": "Feature 2", 0: 'Correlation Coefficient'}, inplace=True)
    df = df.drop(df[df['Correlation Coefficient'] == 1.0].index)
    return df[(df['Feature 1'] == feature) & (df['Correlation Coefficient'] > threshold)]

def correlation_all_vs_all(df, threshold, target_feature):
    pd.set_option('display.max_rows', None)
    df_temp = df.corr().abs().unstack().sort_values(kind="quicksort", ascending=False).reset_index()
    df_temp.rename(columns={"level_0": "Feature 1", "level_1": "Feature 2", 0: 'Correlation Coefficient'}, inplace=True)
    df_temp.drop(df.iloc[1::2].index, inplace=True)
    df_temp = df_temp.drop(df_temp[df_temp['Correlation Coefficient'] == 1.0].index)
    lista_feature1= df_temp['Feature 1']
    lista_feature2= df_temp['Feature 2']
    lista_corr1=[]
    lista_corr2=[]
    for x in lista_feature1:
        lista_corr1.append(np.corrcoef(df[x],df[target_feature])[0][1])
    
    for x in lista_feature2:
        lista_corr2.append(np.corrcoef(df[x],df[target_feature])[0][1])
        
    df_temp['corr1_target']= lista_corr1
    df_temp['corr2_target']= lista_corr2

    return df_temp[df_temp['Correlation Coefficient'] > threshold]

def feature_selector(df, y, threshold_y, threshold_x):

    temp_features_list = correlation_1_vs_all(df, y, threshold_y)['Feature 2'].tolist() # take main variables
    chosen_features = []

    while len(temp_features_list) > 0:

        x = temp_features_list[0]
        chosen_features.append(x)
        temp_features_list.remove(x)
        temp_correlation_list = correlation_1_vs_all(df, x, threshold_x)['Feature 2'].tolist() # take main variables

        for x in temp_correlation_list:
            if x in temp_features_list:
                temp_features_list.remove(x)

    return chosen_features



In [16]:
final_df = pd.read_csv('data/multi_df.csv')

#final_df.to_csv('data/final_df.csv')
final_df.drop(['Unnamed: 0'],axis=1,inplace=True)

final_df

Date  opening_price  highest_price  lowest_price  closing_price  \
0    2019-07-21    8377.213659    8543.047136   8181.097416    8357.655474   
1    2019-07-22    8377.213659    8543.047136   8181.097416    8357.655474   
2    2019-07-23    8377.213659    8543.047136   8181.097416    8357.655474   
3    2019-07-24    8377.213659    8543.047136   8181.097416    8357.655474   
4    2019-07-25    8377.213659    8543.047136   8181.097416    8357.655474   
..          ...            ...            ...           ...            ...   
988  2022-04-04   49850.083260   50921.559187  48406.775364   49657.176863   
989  2022-04-05   49657.250779   50724.222253  48218.449780   49463.149624   
990  2022-04-06   49463.235427   50525.838556  48029.083533   49268.164625   
991  2022-04-07   49268.262838   50326.638605  47838.902608   49072.452236   
992  2022-04-08   49072.563308   50126.856958  47648.137716   48876.246746   

     transactions_in_blockchain  avg_block_size  sent_by_adress  \
0                 313426.314394   736536.531673   398086.453913   
1                 313426.314394   736536.531673   398086.453913   
2                 313426.314394   736536.531673   398086.453913   
3                 313426.314394   736536.531673   398086.453913   
4                 313426.314394   736536.531673   398086.453913   
..                          ...             ...             ...   
988               261465.135608   651208.973739   496796.324165   
989               261220.483127   651122.139053   496462.115067   
990               260975.300563   651041.236898   496127.506798   
991               260729.922985   650966.543424   495793.047903   
992               260484.689343   650898.307072   495459.286032   

     avg_mining_difficulty  avg_hashrate  ...  active_adresses macd  \
0             1.283969e+13  9.369465e+19  ...              0.000000   
1             1.283969e+13  9.369465e+19  ...              0.000000   
2             1.283969e+13  9.369465e+19  ...              0.000000   
3             1.283969e+13  9.369465e+19  ...              0.000000   
4             1.283969e+13  9.369465e+19  ...              0.000000   
..                     ...           ...  ...                   ...   
988           2.374253e+13  1.754350e+20  ...          -1529.878314   
989           2.379877e+13  1.758263e+20  ...          -1650.351440   
990           2.385496e+13  1.762168e+20  ...          -1767.042728   
991           2.391108e+13  1.766062e+20  ...          -1879.843818   
992           2.396713e+13  1.769945e+20  ...          -1988.641017   

     Bull_Bear_Diff hist macd  Bull_Bear_Diff signal macd  \
0                  -11.210430                   -7.644750   
1                  -11.210430                   -7.644750   
2                  -11.210430                   -7.644750   
3                  -11.210430                   -7.644750   
4                  -11.210430                   -7.644750   
..                        ...                         ...   
988                -25.728683                  533.159804   
989                -28.433160                  526.051514   
990                -31.086828                  518.279807   
991                -33.675626                  509.860901   
992                -36.186535                  500.814267   

     Bull_Bear_Diff macd  FUTMSCIACWI hist macd  FUTMSCIACWI signal macd  \
0               0.000000               0.227784                 0.167869   
1               0.000000               0.227784                 0.167869   
2               0.000000               0.227784                 0.167869   
3               0.000000               0.227784                 0.167869   
4               0.000000               0.227784                 0.167869   
..                   ...                    ...                      ...   
988           507.431121              -0.136523                -0.034943   
989           497.618355              -0.140456                -0.070057   

In [17]:
columnas=list(final_df.columns[1:59])

In [18]:
columnas

['opening_price',
 'highest_price',
 'lowest_price',
 'closing_price',
 'transactions_in_blockchain',
 'avg_block_size',
 'sent_by_adress',
 'avg_mining_difficulty',
 'avg_hashrate',
 'mining_profitability',
 'sent_coins_in_usd',
 'avg_transaction_fees',
 'median_transaction_fees',
 'avg_block_time',
 'avg_transaction_value',
 'median_transaction_value',
 'tweets_day',
 'google_trends',
 'active_addresses',
 'top100_to_total_percentage',
 'avg_fee_to_reward',
 'avg_price_usd',
 'market_cap_usd',
 'sf_ratio',
 'number_of_coins_in_circulation',
 'miner_revenue',
 'lbma_gold',
 'VIX_spot',
 'SP500_spot',
 'DXY_spot',
 'MSCIACW_spot',
 'WTI_spot',
 'BDM_spot',
 'FUTWTI',
 'FUT500',
 'FUTGOLD',
 'FUTVIX',
 'FUTBTC',
 'FUTDXY',
 'FUTALT',
 'bc_volatility',
 'ST_UTXOs',
 'tweets_positive_negative_ratio_adj',
 'telegram_positive_ratio_adj',
 'large_holders_netflow',
 'in_out_ratio_adj',
 'profit_losses_ratio_adj',
 'new_addresses',
 'active_adresses',
 'Bull_Bear_Diff',
 'next_day_closing_pric

In [23]:
for x in tqdm(columnas):
    if x!='next_day_closing_price':
        globals()[str(x)+"_df"] = final_df[[x,'next_day_closing_price']]
        final_df.drop([x],inplace=True,axis=1)
        for y in final_df.columns:
            if x.split(" ")[0] == y.split(" ")[0]:
                globals()[str(x)+"_df"][y] = final_df[y]
                final_df.drop([y],inplace=True,axis=1)

100%|██████████████████████████████████████████████████████████████████████████████████| 58/58 [00:19<00:00,  2.92it/s]


In [29]:
correlation_1_vs_all(SP500_spot_df, 'next_day_closing_price', 0)

Feature 1                 Feature 2  \
2761  next_day_closing_price          SP500_spot rsi90   
2766  next_day_closing_price         SP500_spot tema90   
2768  next_day_closing_price                SP500_spot   
2769  next_day_closing_price          SP500_spot tema3   
2771  next_day_closing_price          SP500_spot tema5   
2773  next_day_closing_price          SP500_spot tema7   
2776  next_day_closing_price          SP500_spot dema3   
2777  next_day_closing_price         SP500_spot tema10   
2779  next_day_closing_price          SP500_spot dema5   
2781  next_day_closing_price         SP500_spot tema15   
2783  next_day_closing_price          SP500_spot dema7   
2786  next_day_closing_price         SP500_spot dema10   
2787  next_day_closing_price         SP500_spot dema15   
2790  next_day_closing_price   SP500_spot bband_upper3   
2792  next_day_closing_price           SP500_spot ema3   
2793  next_day_closing_price         SP500_spot tema30   
2796  next_day_closing_price           SP500_spot wma3   
2797  next_day_closing_price   SP500_spot bband_upper5   
2799  next_day_closing_price         SP500_spot dema30   
2802  next_day_closing_price   SP500_spot bband_lower3   
2803  next_day_closing_price           SP500_spot ema5   
2805  next_day_closing_price         SP500_spot dema60   
2808  next_day_closing_price           SP500_spot wma5   
2811  next_day_closing_price   SP500_spot bband_upper7   
2813  next_day_closing_price         SP500_spot tema60   
2816  next_day_closing_price           SP500_spot ema7   
2817  next_day_closing_price         SP500_spot dema90   
2819  next_day_closing_price           SP500_spot wma7   
2821  next_day_closing_price   SP500_spot bband_lower5   
2825  next_day_closing_price  SP500_spot bband_upper10   
2828  next_day_closing_price          SP500_spot ema10   
2830  next_day_closing_price          SP500_spot wma10   
2831  next_day_closing_price   SP500_spot bband_lower7   
2834  next_day_closing_price  SP500_spot bband_upper15   
2836  next_day_closing_price          SP500_spot ema15   
2838  next_day_closing_price          SP500_spot wma15   
2839  next_day_closing_price  SP500_spot bband_lower10   
2849  next_day_closing_price  SP500_spot bband_lower15   
2851  next_day_closing_price          SP500_spot ema30   
2857  next_day_closing_price  SP500_spot bband_upper30   
2862  next_day_closing_price          SP500_spot wma30   
2865  next_day_closing_price  SP500_spot bband_lower30   
2868  next_day_closing_price          SP500_spot ema60   
2872  next_day_closing_price  SP500_spot bband_upper60   
2878  next_day_closing_price  SP500_spot bband_upper90   
2882  next_day_closing_price          SP500_spot wma60   
2884  next_day_closing_price          SP500_spot ema90   
2904  next_day_closing_price          SP500_spot wma90   
2907  next_day_closing_price  SP500_spot bband_lower60   
2954  next_day_closing_price  SP500_spot bband_lower90   
3077  next_day_closing_price           SP500_spot macd   
3080  next_day_closing_price    SP500_spot signal macd   
3099  next_day_closing_price          SP500_spot roc90   
3594  next_day_closing_price      SP500_spot hist macd   
3695  next_day_closing_price          SP500_spot rsi60   
3772  next_day_closing_price        SP500_spot stdev90   
3817  next_day_closing_price          SP500_spot rsi30   
4067  next_day_closing_price          SP500_spot rsi15   
4498  next_day_closing_price          SP500_spot rsi10   
5016  next_day_closing_price           SP500_spot rsi7   
5167  next_day_closing_price           SP500_spot rsi5   
5288  next_day_closing_price           SP500_spot rsi3   
5364  next_day_closing_price          SP500_spot var90   
5637  next_day_closing_price          SP500_spot roc60   
6024  next_day_closing_price          SP500_spot var15   
6027  next_day_closing_price          SP500_spot var10   
6029  next_day_closing_price           SP500_spot var7   
6031  next_day_closing_price           SP500_spot var5   
6035  next_day_cl

In [31]:
correlation_all_vs_all(SP500_spot_df, 0, 'next_day_closing_price') 

Feature 1                 Feature 2  \
86            SP500_spot tema3                SP500_spot   
88            SP500_spot tema5          SP500_spot tema3   
90                  SP500_spot          SP500_spot tema5   
92            SP500_spot tema5          SP500_spot dema3   
94            SP500_spot tema3          SP500_spot dema3   
96                  SP500_spot          SP500_spot dema3   
98            SP500_spot tema7          SP500_spot tema5   
100           SP500_spot dema3          SP500_spot tema7   
102           SP500_spot tema7          SP500_spot tema3   
104           SP500_spot tema7                SP500_spot   
106          SP500_spot tema10          SP500_spot tema7   
108           SP500_spot dema3          SP500_spot dema5   
110          SP500_spot tema10          SP500_spot dema3   
112          SP500_spot tema10          SP500_spot tema5   
114           SP500_spot dema5          SP500_spot tema7   
116           SP500_spot tema5          SP500_spot dema5   
118           SP500_spot dema5          SP500_spot tema3   
120           SP500_spot dema5                SP500_spot   
122           SP500_spot tema3         SP500_spot tema10   
124          SP500_spot tema10          SP500_spot dema5   
126          SP500_spot tema10                SP500_spot   
128           SP500_spot dema7          SP500_spot dema5   
130           SP500_spot dema3          SP500_spot dema7   
132           SP500_spot dema7         SP500_spot tema10   
134          SP500_spot tema10         SP500_spot tema15   
136           SP500_spot tema7          SP500_spot dema7   
138           SP500_spot tema5          SP500_spot dema7   
140           SP500_spot dema7                SP500_spot   
142           SP500_spot tema3          SP500_spot dema7   
144           SP500_spot dema5         SP500_spot tema15   
146           SP500_spot dema7         SP500_spot tema15   
148          SP500_spot dema10          SP500_spot dema7   
150          SP500_spot tema15          SP500_spot tema7   
152           SP500_spot dema3         SP500_spot tema15   
154           SP500_spot tema5         SP500_spot tema15   
156          SP500_spot tema15          SP500_spot tema3   
158                 SP500_spot         SP500_spot tema15   
160           SP500_spot dema5         SP500_spot dema10   
162          SP500_spot dema10         SP500_spot tema15   
164           SP500_spot dema3         SP500_spot dema10   
166          SP500_spot tema10         SP500_spot dema10   
168           SP500_spot tema7         SP500_spot dema10   
170                 SP500_spot         SP500_spot dema10   
172          SP500_spot dema10          SP500_spot tema3   
174           SP500_spot tema5         SP500_spot dema10   
176            SP500_spot wma3           SP500_spot ema3   
178          SP500_spot dema10         SP500_spot dema15   
180    SP500_spot bband_upper3           SP500_spot ema3   
182            SP500_spot wma3   SP500_spot bband_upper3   
184            SP500_spot wma3   SP500_spot bband_lower3   
186            SP500_spot wma5   SP500_spot bband_lower3   
188            SP500_spot ema3         SP500_spot dema10   
190            SP500_spot ema3          SP500_spot dema7   
192           SP500_spot dema7         SP500_spot dema15   
194            SP500_spot wma3          SP500_spot dema7   
196    SP500_spot bband_lower3           SP500_spot ema3   
198           SP500_spot dema5           SP500_spot ema3   
200            SP500_spot wma3         SP500_spot dema10   
202            SP500_spot ema5           SP500_spot ema7   
204           SP500_spot dema5           SP500_spot wma3   
206            SP500_spot ema3           SP500_spot ema5   
208           SP500_spot dema3           SP500_spot ema3   
210                 SP500_spot           SP500_spot ema3   
212            SP500_spot ema3          SP500_spot tema3   
214           SP500_spot tema5           SP500_spot ema3   
216            SP500_spot wma3          SP500_spot dema3   
2

In [53]:
feature_selector(SP500_spot_df, 'next_day_closing_price', 0,0.9)[0:2]

['SP500_spot rsi90', 'SP500_spot tema90']

In [56]:
# Cogemos las 2 principlaes variables que no esten correlacionadas entre ellas en mas de 0.9

for x in tqdm(columnas):
    if x!='next_day_closing_price':

        for y in feature_selector(globals()[(str(x)+"_df")], 'next_day_closing_price', 0,0.9)[0:2]:
            final_df[y] =  globals()[(str(x)+"_df")][y]


100%|██████████████████████████████████████████████████████████████████████████████████| 58/58 [00:11<00:00,  5.09it/s]


In [57]:
final_df

Date  next_day_closing_price  opening_price bband_upper90  \
0    2019-07-21                 10412.5                  8374.800462   
1    2019-07-22                  9888.7                  8374.800462   
2    2019-07-23                  9804.3                  8374.800462   
3    2019-07-24                  9945.3                  8374.800462   
4    2019-07-25                  9831.0                  8374.800462   
5    2019-07-26                  9492.1                  8374.800462   
6    2019-07-27                  9727.8                  8374.800462   
7    2019-07-28                  9580.9                  8374.800462   
8    2019-07-29                  9580.7                  8374.800462   
9    2019-07-30                 10082.0                  8374.800462   
10   2019-07-31                 10380.0                  8374.800462   
11   2019-08-01                 10520.1                  8374.800462   
12   2019-08-02                 10815.7                  8374.800462   
13   2019-08-03                 10934.6                  8374.800462   
14   2019-08-04                 11816.8                  8374.800462   
15   2019-08-05                 11480.9                  8374.800462   
16   2019-08-06                 12013.9                  8374.800462   
17   2019-08-07                 12191.6                  8374.800462   
18   2019-08-08                 12089.8                  8374.800462   
19   2019-08-09                 11314.5                  8374.800462   
20   2019-08-10                 11517.2                  8374.800462   
21   2019-08-11                 11394.2                  8374.800462   
22   2019-08-12                 10892.9                  8374.800462   
23   2019-08-13                 10049.4                  8374.800462   
24   2019-08-14                 10303.4                  8374.800462   
25   2019-08-15                 10335.6                  8374.800462   
26   2019-08-16                 10218.1                  8374.800462   
27   2019-08-17                 10312.7                  8374.800462   
28   2019-08-18                 10910.7                  8374.800462   
29   2019-08-19                 10752.6                  8374.800462   
30   2019-08-20                 10141.5                  8374.800462   
31   2019-08-21                 10105.0                  8374.800462   
32   2019-08-22                 10388.7                  8374.800462   
33   2019-08-23                 10131.0                  8374.800462   
34   2019-08-24                 10136.3                  8374.800462   
35   2019-08-25                 10371.8                  8374.800462   
36   2019-08-26                 10184.8                  8374.800462   
37   2019-08-27                  9729.4                  8374.800462   
38   2019-08-28                  9491.0                  8374.800462   
39   2019-08-29                  9585.4                  8374.800462   
40   2019-08-30                  9594.4                  8374.800462   
41   2019-08-31                  9729.3                  8374.800462   
42   2019-09-01                 10348.8                  8374.800462   
43   2019-09-02                 10612.3                  8374.800462   
44   2019-09-03                 10568.2                  8374.800462   
45   2019-09-04                 10566.9                  8374.800462   
46   2019-09-05                 10309.3                  8374.800462   
47   2019-09-06                 10461.1                  8374.800462   
48   2019-09-07                 10402.8                  8374.800462   
49   2019-09-08                 10309.0                  8374.800462   
50   2019-09-09                 10105.4                  8374.800462   
51   2019-09-10                 10162.5                  8374.800462   
52   2019-09-11                 10415.1                  8374.800462   
53   2019-09-12                 10342.1                  8374.800462   
54   2019-09-13                 10337.3            

In [61]:
final_df.to_csv('data/2_de_cada.csv')